# Regressão Linear Múltipla


In [146]:
import pandas as pd
import numpy as np

import feature_engine.missing_data_imputers as mdi
from feature_engine import categorical_encoders as ce
from feature_engine import variable_transformers as vt

from sklearn.pipeline import Pipeline
from sklearn import metrics
from sklearn import linear_model
from sklearn import model_selection
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt
from pandas_profiling import ProfileReport

import xgboost as xgb


In [ ]:
df = pd.read_csv('dados_preco.csv')

In [2]:
df

descricao               criado  \
0                 30 CAP | BUPROPIONA CLORIDRATO  150MG  2020-08-05 23:19:09   
1                        60 CAP | FINASTERIDA 1:10  1MG  2020-08-05 22:51:09   
2     60 CAP | NAC  250MG; SILIMARINA  150MG; SAME  ...  2020-08-05 22:51:09   
3                      60 CAP | ANASTROZOL 1:10 0.300MG  2020-08-05 22:51:09   
4        120 CAP | DUTASTERIDA 0.250MG; TADALAFIL  10MG  2020-08-05 22:49:09   
...                                                 ...                  ...   
7116  45 CAP | SERTRALINA CLORIDRATO  40MG; SLENDEST...  2020-07-09 17:33:11   
7117                       120 CAP | GREENSELECT  120MG  2020-07-09 17:24:09   
7118  60 CAP | MAGNESIO QUELADO 30%  220MG; SELENIO ...  2020-07-09 17:23:10   
7119  30 CAP | VALERIANA  50MG; PASSIFLORA  500MG; C...  2020-07-09 17:22:09   
7120  60 CAP | ACIDO TRANEXAMICO  200MG; BIOTINA 2.5...  2020-07-09 17:14:09   

      qtdInsumos  calculado  correto  
0              1    47.5297     39.9  
1              1    46.9620     43.6  
2              3   105.1390    111.4  
3              1    49.0314     43.6  
4              2   161.8272    146.0  
...          ...        ...      ...  
7116          12   188.5325    181.8  
7117           1   377.6529    346.6  
7118          11   166.2868    157.2  
7119           3    60.1646     68.1  
7120           2   107.0370     95.3  

[7121 rows x 5 columns]

In [3]:
profile = ProfileReport(df, title='Entendendo os dados',html={'style':{'full_width':True}})
profile.to_notebook_iframe()

Render HTML: 100%|██████████| 1/1 [00:00<00:00,  1.13it/s]


In [82]:
ingr = df['descricao']
ingr

0                   30 CAP | BUPROPIONA CLORIDRATO  150MG
1                          60 CAP | FINASTERIDA 1:10  1MG
2       60 CAP | NAC  250MG; SILIMARINA  150MG; SAME  ...
3                        60 CAP | ANASTROZOL 1:10 0.300MG
4          120 CAP | DUTASTERIDA 0.250MG; TADALAFIL  10MG
                              ...                        
7116    45 CAP | SERTRALINA CLORIDRATO  40MG; SLENDEST...
7117                         120 CAP | GREENSELECT  120MG
7118    60 CAP | MAGNESIO QUELADO 30%  220MG; SELENIO ...
7119    30 CAP | VALERIANA  50MG; PASSIFLORA  500MG; C...
7120    60 CAP | ACIDO TRANEXAMICO  200MG; BIOTINA 2.5...
Name: descricao, Length: 7121, dtype: object

In [123]:
df[['cap', 'ingredientes']] = df['descricao'].str.split('|', 1, expand=True)


In [153]:
df['cap'] = df['cap'].str.replace('CAP','').astype(int)

In [85]:
dfi = df['ingredientes'].str.split(';', -1, expand=True)
dfi

0                        1   \
0      BUPROPIONA CLORIDRATO  150MG                     None   
1             FINASTERIDA 1:10  1MG                     None   
2                        NAC  250MG        SILIMARINA  150MG   
3           ANASTROZOL 1:10 0.300MG                     None   
4               DUTASTERIDA 0.250MG          TADALAFIL  10MG   
...                             ...                      ...   
7116    SERTRALINA CLORIDRATO  40MG          SLENDESTA  75MG   
7117             GREENSELECT  120MG                     None   
7118    MAGNESIO QUELADO 30%  220MG   SELENIO QUELADO  80MCG   
7119                VALERIANA  50MG        PASSIFLORA  500MG   
7120       ACIDO TRANEXAMICO  200MG          BIOTINA 2.500MG   

                                         2                        3   \
0                                      None                     None   
1                                      None                     None   
2                                SAME  50MG                     None   
3                                      None                     None   
4                                      None                     None   
...                                     ...                      ...   
7116   TRIMETILXANTINA MICROENCAPSULA  90MG       PHOLIAMAGRA  100MG   
7117                                   None                     None   
7118                      CROMO GTF  250MCG   TRANSRESVERATROL  30MG   
7119               CAMOMILA EXT SECO  500MG                     None   
7120                                   None                     None   

                      4                     5                       6   \
0                   None                  None                    None   
1                   None                  None                    None   
2                   None                  None                    None   
3                   None                  None                    None   
4                   None                  None                    None   
...                  ...                   ...                     ...   
7116      ORLISTAT  60MG          ALOINA  25MG    CLORTALIDONA 7.500MG   
7117                None                  None                    None   
7118   QUERCETINA  200MG   ZINCO QUELADO  15MG   COBRE QUELADO 0.600MG   
7119                None                  None                    None   
7120                None                  None                    None   

                             7                 8                       9   \
0                          None              None                    None   
1                          None              None                    None   
2                          None              None                    None   
3                          None              None                    None   
4                          None              None                    None   
...                         ...               ...                     ...   
7116      ESPIRONOLACTONA  25MG        KCL  300MG       CROMO GTF  150MCG   
7117                       None              None                    None   
7118   METILFOLATO 1:10 0.400MG   VIT B12  100MCG   MANGANES QUELADO  1MG   
7119                       None              None                    None   
7120                       None              None                    None   

      ...    16    17    18    19    20    21    22    23    24    25  
0     ...  None  None  None  None  None  None  None  None  None  None  
1     ...  None  None  None  None  None  None  None  None  None  None  
2     ...  None  None  None  None  None  None  None  None  None  None  
3     ...  None  None  None  None  None  None  None  None  None  None  
4     ...  None  None  None  None  None  None  None  None  None  None  
...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
7116  ...  None  None  None  None  None  None  None  None  None  None  
7117  ...

In [25]:
def reversed_string(a_string):
    return a_string[::-1]

In [39]:
reversed_string(reversed_string(dfi[0][0]).split(' ', 1)[0]).strip()
reversed_string(reversed_string(dfi[0][0]).split(' ', 1)[1]).strip()

'BUPROPIONA CLORIDRATO'

In [117]:
for i in range(len(dfi)) :
    for j in range(len(dfi.columns)):
        if dfi.iat[i,j] is not None:
            coluna=reversed_string(reversed_string(dfi.iat[i,j]).split(' ', 1)[1]).strip()
            qtde = reversed_string(reversed_string(dfi.iat[i,j]).split(' ', 1)[0]).strip()
            if 'MCG' in qtde:
                qtde_val=float(qtde.replace('MCG',''))* 0.000001
            elif 'MG' in qtde:
                qtde_val=float(qtde.replace('MG',''))* 0.001
            elif 'G' in qtde:
                qtde_val=float(qtde.replace('G',''))
            elif 'UN' in qtde:
                qtde_val=float(qtde.replace('UN',''))
            elif 'UI' in qtde:
                qtde=qtde.replace('%','')
                qtde_val=float(qtde.replace('UI',''))
            elif 'CAP' in qtde:
                qtde_val=float(qtde.replace('CAP',''))
            elif '%' in qtde:
                qtde_val=float(qtde.replace('%',''))
            elif 'UTR' in qtde:
                qtde_val=float(qtde.replace('UTR',''))
            else:
                qtde_val=float(qtde)

            df.at[i,coluna]= qtde_val

In [125]:
df

descricao               criado  \
0                 30 CAP | BUPROPIONA CLORIDRATO  150MG  2020-08-05 23:19:09   
1                        60 CAP | FINASTERIDA 1:10  1MG  2020-08-05 22:51:09   
2     60 CAP | NAC  250MG; SILIMARINA  150MG; SAME  ...  2020-08-05 22:51:09   
3                      60 CAP | ANASTROZOL 1:10 0.300MG  2020-08-05 22:51:09   
4        120 CAP | DUTASTERIDA 0.250MG; TADALAFIL  10MG  2020-08-05 22:49:09   
...                                                 ...                  ...   
7116  45 CAP | SERTRALINA CLORIDRATO  40MG; SLENDEST...  2020-07-09 17:33:11   
7117                       120 CAP | GREENSELECT  120MG  2020-07-09 17:24:09   
7118  60 CAP | MAGNESIO QUELADO 30%  220MG; SELENIO ...  2020-07-09 17:23:10   
7119  30 CAP | VALERIANA  50MG; PASSIFLORA  500MG; C...  2020-07-09 17:22:09   
7120  60 CAP | ACIDO TRANEXAMICO  200MG; BIOTINA 2.5...  2020-07-09 17:14:09   

      qtdInsumos  calculado  correto    cap  \
0              1    47.5297     39.9   30     
1              1    46.9620     43.6   60     
2              3   105.1390    111.4   60     
3              1    49.0314     43.6   60     
4              2   161.8272    146.0  120     
...          ...        ...      ...    ...   
7116          12   188.5325    181.8   45     
7117           1   377.6529    346.6  120     
7118          11   166.2868    157.2   60     
7119           3    60.1646     68.1   30     
7120           2   107.0370     95.3   60     

                                           ingredientes BUPROPIONA CLORIDRATO  \
0                          BUPROPIONA CLORIDRATO  150MG                  0.15   
1                                 FINASTERIDA 1:10  1MG                   NaN   
2             NAC  250MG; SILIMARINA  150MG; SAME  50MG                   NaN   
3                               ANASTROZOL 1:10 0.300MG                   NaN   
4                  DUTASTERIDA 0.250MG; TADALAFIL  10MG                   NaN   
...                                                 ...                   ...   
7116   SERTRALINA CLORIDRATO  40MG; SLENDESTA  75MG;...                   NaN   
7117                                 GREENSELECT  120MG                   NaN   
7118   MAGNESIO QUELADO 30%  220MG; SELENIO QUELADO ...                   NaN   
7119   VALERIANA  50MG; PASSIFLORA  500MG; CAMOMILA ...                   NaN   
7120          ACIDO TRANEXAMICO  200MG; BIOTINA 2.500MG                   NaN   

     FINASTERIDA 1:10   NAC  ... GLICERINA ALOE VERA EXT GLICOLICO PCA-NA  \
0                 NaN   NaN  ...       NaN                     NaN    NaN   
1               0.001   NaN  ...       NaN                     NaN    NaN   
2                 NaN  0.25  ...       NaN                     NaN    NaN   
3                 NaN   NaN  ...       NaN                     NaN    NaN   
4                 NaN   NaN  ...       NaN                     NaN    NaN   
...               ...   ...  ...       ...                     ...    ...   
7116              NaN   NaN  ...       NaN                     NaN    NaN   
7117              NaN   NaN  ...       NaN                     NaN    NaN   
7118              NaN   NaN  ...       NaN                     NaN    NaN   
7119              NaN   NaN  ...       NaN                     NaN    NaN   
7120              NaN   NaN  ...       NaN                     NaN    NaN   

     GENTAMICINA SULFATO BASE CREME DLFENILALANINA BACTEROIDES FRAGILIS  \
0                    NaN        NaN            NaN                  NaN   
1                    NaN        NaN            NaN                  NaN   
2                    NaN        NaN            NaN                  NaN   
3                    NaN        NaN            NaN                  NaN   
4                    NaN        NaN            NaN                  NaN   
...                  ...        ...            ...                  ...   
7116                 NaN        NaN            NaN                  NaN   
7117                 N

In [143]:
df = df.fillna(0)

In [154]:
df.dtypes.head(10)

descricao                 object
criado                    object
qtdInsumos                 int64
calculado                float64
correto                  float64
cap                        int32
ingredientes              object
BUPROPIONA CLORIDRATO    float64
FINASTERIDA 1:10         float64
NAC                      float64
dtype: object

In [112]:
df.to_excel("df_variaveis.xlsx")

In [155]:
train, test = train_test_split(df, test_size=2000, random_state=42)
Y_train=train['correto']
X_train=train[train.columns[~train.columns.isin(['descricao','criado','calculado','correto','ingredientes'])]]

Y_test=test['correto']
X_test=test[test.columns[~test.columns.isin(['descricao','criado','calculado','correto','ingredientes'])]]

In [156]:
X_train

qtdInsumos  cap  BUPROPIONA CLORIDRATO  FINASTERIDA 1:10  NAC  \
5627           1  270                    0.0               0.0  0.0   
6381           1   60                    0.0               0.0  0.0   
509            2   60                    0.0               0.0  0.0   
6138          11   90                    0.0               0.0  0.0   
5102           1  180                    0.0               0.0  0.0   
...          ...  ...                    ...               ...  ...   
3772           2   90                    0.0               0.0  0.0   
5191           1   40                    0.0               0.0  0.0   
5226           1   60                    0.0               0.0  0.0   
5390           4   30                    0.0               0.0  0.0   
860            3   60                    0.0               0.0  0.0   

      SILIMARINA  SAME  ANASTROZOL 1:10  DUTASTERIDA  TADALAFIL  ...  \
5627         0.0   0.0              0.0          0.0        0.0  ...   
6381         0.0   0.0              0.0          0.0        0.0  ...   
509          0.0   0.0              0.0          0.0        0.0  ...   
6138         0.0   0.0              0.0          0.0        0.0  ...   
5102         0.0   0.0              0.0          0.0        0.0  ...   
...          ...   ...              ...          ...        ...  ...   
3772         0.0   0.0              0.0          0.0        0.0  ...   
5191         0.0   0.0              0.0          0.0        0.0  ...   
5226         0.0   0.0              0.0          0.0        0.0  ...   
5390         0.0   0.0              0.0          0.0        0.0  ...   
860          0.0   0.0              0.0          0.0        0.0  ...   

      GLICERINA  ALOE VERA EXT GLICOLICO  PCA-NA  GENTAMICINA SULFATO  \
5627        0.0                      0.0     0.0                  0.0   
6381        0.0                      0.0     0.0                  0.0   
509         0.0                      0.0     0.0                  0.0   
6138        0.0                      0.0     0.0                  0.0   
5102        0.0                      0.0     0.0                  0.0   
...         ...                      ...     ...                  ...   
3772        0.0                      0.0     0.0                  0.0   
5191        0.0                      0.0     0.0                  0.0   
5226        0.0                      0.0     0.0                  0.0   
5390        0.0                      0.0     0.0                  0.0   
860         0.0                      0.0     0.0                  0.0   

      BASE CREME  DLFENILALANINA  BACTEROIDES FRAGILIS  ANDARINE  L-PROLINA  \
5627         0.0             0.0                   0.0       0.0        0.0   
6381         0.0             0.0                   0.0       0.0        0.0   
509          0.0             0.0                   0.0       0.0        0.0   
6138         0.0             0.0                   0.0       0.0        0.0   
5102         0.0             0.0                   0.0       0.0        0.0   
...          ...             ...                   ...       ...        ...   
3772         0.0             0.0                   0.0       0.0        0.0   
5191         0.0             0.0                   0.0       0.0        0.0   
5226         0.0             0.0                   0.0       0.0        0.0   
5390         0.0             0.0                   0.0       0.0        0.0   
860          0.0             0.0                   0.0       0.0        0.0   

      TRIMETILXANTINA MICROENCAPSULA  
5627                             0.0  
6381                             0.0  
509                              0.0  
6138                             0.0  
5102                             0.0  
...                              ...  
3772                             0.0  
5191                             0.0  
5226                             0.0  
5390                             0.0  
860                              

In [157]:
model_xgb = xgb.XGBRegressor(random_state=1992)

full_pipeline_xgb = Pipeline( steps=[('modelo', model_xgb)])

param_grid = { "modelo__n_estimators":[100],    #90,100,110
               "modelo__max_depth":[4],    #,5,6
               "modelo__eta":[0.05],     #  ,0.1, 0.15
               "modelo__subsample":[0.85] }   # , 0.9,0.95

search_xgb = model_selection.GridSearchCV(full_pipeline_xgb,
                                          param_grid,
                                          cv=3,
                                          n_jobs=-1,
                                          scoring='neg_root_mean_squared_error') #Declaração

search_xgb.fit(X_train, Y_train) #Executa o treinamento!!

best_model_xgb = search_xgb.best_estimator_

In [161]:
y_train_xgb = best_model_xgb.predict(X_train)

C:\Users\csati\AppData\Local\Programs\Python\Python37\lib\site-packages\xgboost\data.py:114: UserWarning: Use subset (sliced data) of np.ndarray is not recommended because it will generate extra copies and increase memory consumption
  "because it will generate extra copies and increase " +


In [159]:
y_test_xgb = best_model_xgb.predict(X_test)

In [160]:
y_test_xgb

array([355.99362 ,  77.534546, 114.7336  , ...,  78.80728 , 167.28667 ,
       117.766365], dtype=float32)

In [174]:
df_excel = Y_train

In [177]:
df_excel['treino']=y_train_xgb

C:\Users\csati\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [179]:
y_excel  = pd.DataFrame(y_train_xgb)

df_out = X_test.reset_index()
df_out["correto"] = Y_test.reset_index()["correto"]
df_out["Prediction"] = y_excel.reset_index()[0]


Y_test['preds'] = y_excel

df_out = pd.merge(df,Y_test[['preds']],how = 'left',left_index = True, right_index = True)

C:\Users\csati\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
C:\Users\csati\AppData\Local\Programs\Python\Python37\lib\site-packages\pandas\core\indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  iloc._setitem_with_indexer(indexer, value)
C:\Users\csati\AppData\Roaming\Python\Python37\site-packages\IPython\core\interactiveshell.py:3437: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#ret

In [180]:
df_out

descricao               criado  \
0                 30 CAP | BUPROPIONA CLORIDRATO  150MG  2020-08-05 23:19:09   
1                        60 CAP | FINASTERIDA 1:10  1MG  2020-08-05 22:51:09   
2     60 CAP | NAC  250MG; SILIMARINA  150MG; SAME  ...  2020-08-05 22:51:09   
3                      60 CAP | ANASTROZOL 1:10 0.300MG  2020-08-05 22:51:09   
4        120 CAP | DUTASTERIDA 0.250MG; TADALAFIL  10MG  2020-08-05 22:49:09   
...                                                 ...                  ...   
7116  45 CAP | SERTRALINA CLORIDRATO  40MG; SLENDEST...  2020-07-09 17:33:11   
7117                       120 CAP | GREENSELECT  120MG  2020-07-09 17:24:09   
7118  60 CAP | MAGNESIO QUELADO 30%  220MG; SELENIO ...  2020-07-09 17:23:10   
7119  30 CAP | VALERIANA  50MG; PASSIFLORA  500MG; C...  2020-07-09 17:22:09   
7120  60 CAP | ACIDO TRANEXAMICO  200MG; BIOTINA 2.5...  2020-07-09 17:14:09   

      qtdInsumos  calculado  correto_x  cap  \
0              1    47.5297       39.9   30   
1              1    46.9620       43.6   60   
2              3   105.1390      111.4   60   
3              1    49.0314       43.6   60   
4              2   161.8272      146.0  120   
...          ...        ...        ...  ...   
7116          12   188.5325      181.8   45   
7117           1   377.6529      346.6  120   
7118          11   166.2868      157.2   60   
7119           3    60.1646       68.1   30   
7120           2   107.0370       95.3   60   

                                           ingredientes  \
0                          BUPROPIONA CLORIDRATO  150MG   
1                                 FINASTERIDA 1:10  1MG   
2             NAC  250MG; SILIMARINA  150MG; SAME  50MG   
3                               ANASTROZOL 1:10 0.300MG   
4                  DUTASTERIDA 0.250MG; TADALAFIL  10MG   
...                                                 ...   
7116   SERTRALINA CLORIDRATO  40MG; SLENDESTA  75MG;...   
7117                                 GREENSELECT  120MG   
7118   MAGNESIO QUELADO 30%  220MG; SELENIO QUELADO ...   
7119   VALERIANA  50MG; PASSIFLORA  500MG; CAMOMILA ...   
7120          ACIDO TRANEXAMICO  200MG; BIOTINA 2.500MG   

      BUPROPIONA CLORIDRATO  FINASTERIDA 1:10   NAC  ...  \
0                      0.15             0.000  0.00  ...   
1                      0.00             0.001  0.00  ...   
2                      0.00             0.000  0.25  ...   
3                      0.00             0.000  0.00  ...   
4                      0.00             0.000  0.00  ...   
...                     ...               ...   ...  ...   
7116                   0.00             0.000  0.00  ...   
7117                   0.00             0.000  0.00  ...   
7118                   0.00             0.000  0.00  ...   
7119                   0.00             0.000  0.00  ...   
7120                   0.00             0.000  0.00  ...   

      ALOE VERA EXT GLICOLICO  PCA-NA  GENTAMICINA SULFATO  BASE CREME  \
0                         0.0     0.0                  0.0         0.0   
1                         0.0     0.0                  0.0         0.0   
2                         0.0     0.0                  0.0         0.0   
3                         0.0     0.0                  0.0         0.0   
4                         0.0     0.0                  0.0         0.0   
...                       ...     ...                  ...         ...   
7116                      0.0     0.0                  0.0         0.0   
7117                      0.0     0.0                  0.0         0.0   
7118                      0.0     0.0                  0.0         0.0   
7119                      0.0     0.0                  0.0         0.0   
7120                      0.0     0.0                  0.0         0.0   

      DLFENILALANINA  BACTEROIDES FRAGILIS  ANDARINE  L-PROLINA  \
0                0.0                   0.0       0.0        0.0   
1                0.0                   0.0       0.0        0.0   


C:\Users\csati\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [176]:
df_excel

5627                                                  100.6
6381                                                     44
509                                                    78.6
6138                                                    884
5102                                                     51
                                ...                        
5191                                                   56.8
5226                                                    302
5390                                                     52
860                                                   125.1
treino    0       143.639053
1        99.537704
2       ...
Name: correto, Length: 5122, dtype: object

## Definição dos tipos de variáveis

In [56]:
target = 'mpg' # Milhas por galão
num_vars = ['cylinders', 'displacement', 'horsepower', 'weight', 'acceleration', 'year']
cat_vars = ['origin']

auto_df[cat_vars] = auto_df[cat_vars].astype(str)

NameError: name 'auto_df' is not defined

## Seprando em base de treino e teste

In [ ]:
auto_df.dtypes

mpg             float64
cylinders         int64
displacement    float64
horsepower        int64
weight            int64
acceleration    float64
year              int64
origin           object
name             object
dtype: object

In [ ]:
X_train, X_test, y_train, y_test = model_selection.train_test_split( auto_df[num_vars+cat_vars],
                                                                     auto_df[target],
                                                                     random_state=1992,
                                                                     test_size=0.25)

In [ ]:
y_test

65     17.0
148    26.0
366    29.0
11     14.0
316    29.8
       ... 
172    18.0
121    24.0
257    20.8
305    26.8
13     14.0
Name: mpg, Length: 98, dtype: float64

## Estatísticas descritivas

In [ ]:
profile = ProfileReport(X_train, title='Entendendo autos',html={'style':{'full_width':True}})
profile.to_notebook_iframe()

Render HTML: 100%|██████████| 1/1 [00:03<00:00,  3.74s/it]


## Definição do Pipeline para transformações...

In [ ]:
log = vt.LogTransformer(variables=num_vars) # Define o transformador do transformação logaritmica
onehot = ce.OneHotCategoricalEncoder(variables=cat_vars, drop_last=True) # Cria Dummys
model = linear_model.Lasso() # Definição do modelo

full_pipeline = Pipeline( steps=[
    ("log", log),
    ("onehot", onehot),
    ('model', model) ] )

param_grid = { 'model__alpha':[0.0167, 0.0001, 0.001, 0.01, 0.1, 0.2, 0.5, 0.8, 1], # linspace    lambda
               'model__normalize':[True],
               'model__random_state':[1992]}

search = model_selection.GridSearchCV(full_pipeline,
                                          param_grid,
                                          cv=5,
                                          n_jobs=-1,
                                          scoring='neg_root_mean_squared_error')

search.fit(X_train, y_train) # Executa o treinamento!!

best_model = search.best_estimator_

In [ ]:
best_model

Pipeline(steps=[('log',
                 LogTransformer(variables=['cylinders', 'displacement',
                                           'horsepower', 'weight',
                                           'acceleration', 'year'])),
                ('onehot',
                 OneHotCategoricalEncoder(drop_last=True,
                                          variables=['origin'])),
                ('model',
                 Lasso(alpha=0.001, normalize=True, random_state=1992))])

## Resultados obtidos

In [ ]:
cv_result = pd.DataFrame(search.cv_results_) # Pega resultdos do grid
cv_result = cv_result.sort_values(by='mean_test_score', ascending = False,)

## Checando performance na base de teste

In [ ]:
# Verificando erro na base de teste
y_test_pred = best_model.predict(X_test)
root_mean_squadred_erro = metrics.mean_squared_error( y_test, y_test_pred) ** (1/2)
print( "Raiz do Erro Quadrático Médio:", root_mean_squadred_erro)

Raiz do Erro Quadrático Médio: 2.821885214125986


## Retreinar para a base toda?

In [ ]:
best_model.fit( auto_df[num_vars+cat_vars], auto_df[target] )

Pipeline(steps=[('log',
                 LogTransformer(variables=['cylinders', 'displacement',
                                           'horsepower', 'weight',
                                           'acceleration', 'year'])),
                ('onehot',
                 OneHotCategoricalEncoder(drop_last=True,
                                          variables=['origin'])),
                ('model',
                 Lasso(alpha=0.001, normalize=True, random_state=1992))])

## Salvando modelo no 'disco'

In [ ]:
model_s = pd.Series( {"cat_vars":cat_vars,
                      "num_vars":num_vars,
                      "fit_vars": X_train.columns.tolist(),
                      "model":best_model,
                      "rmse":root_mean_squadred_erro} )

model_s.to_pickle("best_model_auto.pkl")

In [ ]:
model_s

cat_vars                                             [origin]
num_vars    [cylinders, displacement, horsepower, weight, ...
fit_vars    [cylinders, displacement, horsepower, weight, ...
model       (LogTransformer(variables=['cylinders', 'displ...
rmse                                                  2.82189
dtype: object